In [10]:
from langchain import PromptTemplate
from langchain.chains import RetrievalQA
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.vectorstores import Pinecone
import pinecone
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.prompts import PromptTemplate
from langchain.llms import  ctransformers
import os
import numpy as np
import pickle

## **Extract data from the PDF**

In [11]:
def load_pdf(data):
    loader=DirectoryLoader(data,
                    glob="*.pdf",
                    loader_cls=PyPDFLoader)

    documents=loader.load()

    return documents

In [12]:
extracted_data = load_pdf("E:\AI & Machine Learning\LLM,OpenAI\End-to-End-Medical-Chatbot\data")

In [13]:
extracted_data

[Document(page_content='', metadata={'source': 'E:\\AI & Machine Learning\\LLM,OpenAI\\End-to-End-Medical-Chatbot\\data\\Medical_book.pdf', 'page': 0}),
 Document(page_content='TheGALE\nENCYCLOPEDIA\nofMEDICINE\nSECOND EDITION', metadata={'source': 'E:\\AI & Machine Learning\\LLM,OpenAI\\End-to-End-Medical-Chatbot\\data\\Medical_book.pdf', 'page': 1}),
 Document(page_content='TheGALE\nENCYCLOPEDIA\nofMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, EDITOR\nDEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR\nVOLUME\nA-B1', metadata={'source': 'E:\\AI & Machine Learning\\LLM,OpenAI\\End-to-End-Medical-Chatbot\\data\\Medical_book.pdf', 'page': 2}),
 Document(page_content='STAFF\nJacqueline L. Longe, Project Editor\nDeirdre S. Blanchfield, Associate Editor\nChristine B. Jeryan, Managing Editor\nDonna Olendorf, Senior Editor\nStacey Blachford, Associate Editor\nKate Kretschmann, Melissa C. McDade, Ryan\nThomason, Assistant Editors\nMark Springer, Technical Specialist\nAndrea Lopeman, Programmer/Analyst

## **Text preprocessing**

In [14]:
import re
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import sent_tokenize

# Download necessary resources
nltk.download('stopwords')
nltk.download('punkt')

# Define preprocessing functions
def clean_text(text):
    # Remove non-alphanumeric characters but keep URLs intact
    text = re.sub(r'[^\w\s\./-]', '', text)
    text = ' '.join(text.split())
    return text

def lowercase_text(text):
    # Convert text to lowercase
    return text.lower()

def remove_stopwords(text):
    # Remove stopwords from the text (excluding URLs)
    stop_words = set(stopwords.words('english'))
    tokens = text.split()
    filtered_tokens = [token for token in tokens if token.lower() not in stop_words and not re.match(r'^https?://', token)]
    return ' '.join(filtered_tokens)

# Apply preprocessing to each document
preprocessed_documents = []
for document in extracted_data:
    content = document.page_content
    # Clean text (keeping URLs)
    cleaned_content = clean_text(content)
    # Lowercase text
    lowercase_content = lowercase_text(cleaned_content)
    # Remove stopwords (excluding URLs)
    filtered_content = remove_stopwords(lowercase_content)
    # Update the 'page_content' attribute of the document with preprocessed text
    document.page_content = filtered_content
    # Append the preprocessed document to the list
    preprocessed_documents.append(document)


AttributeError: module 'numpy' has no attribute 'int'.
`np.int` was a deprecated alias for the builtin `int`. To avoid this error in existing code, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
The aliases was originally deprecated in NumPy 1.20; for more details and guidance see the original release note at:
    https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations

In [ ]:
len(preprocessed_documents)

637

In [9]:
preprocessed_documents

NameError: name 'preprocessed_documents' is not defined

## **Create text chunks**

In [9]:
def text_split(preprocessed_documents):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
    text_chunks = text_splitter.split_documents(preprocessed_documents)  # Wrap extracted_data in a list
    return text_chunks

text_chunks=text_split(list(preprocessed_documents))
print("length of text_chunks:",len(text_chunks))

length of text_chunks: 4564


In [10]:
text_chunks

[Document(page_content='thegale encyclopedia ofmedicine second edition', metadata={'source': '/media/supunlakshan/Learning Hub/AI & Machine Learning/LLM,OpenAI/End-to-End-Medical-Chatbot/data/Medical_book.pdf', 'page': 1}),
 Document(page_content='thegale encyclopedia ofmedicine second edition jacqueline l. longe editor deirdre s. blanchfield associate editor volume a-b1', metadata={'source': '/media/supunlakshan/Learning Hub/AI & Machine Learning/LLM,OpenAI/End-to-End-Medical-Chatbot/data/Medical_book.pdf', 'page': 2}),
 Document(page_content='staff jacqueline l. longe project editor deirdre s. blanchfield associate editor christine b. jeryan managing editor donna olendorf senior editor stacey blachford associate editor kate kretschmann melissa c. mcdade ryan thomason assistant editors mark springer technical specialist andrea lopeman programmer/analyst barbara j. yarrow manager imaging multimedia content robyn v . young project manager imaging multimedia content dean dauphinais senio

In [11]:

print("Length of text_chunks:", len(text_chunks))
print(type(text_chunks))

Length of text_chunks: 4564
<class 'list'>


In [12]:
text_chunks

[Document(page_content='thegale encyclopedia ofmedicine second edition', metadata={'source': '/media/supunlakshan/Learning Hub/AI & Machine Learning/LLM,OpenAI/End-to-End-Medical-Chatbot/data/Medical_book.pdf', 'page': 1}),
 Document(page_content='thegale encyclopedia ofmedicine second edition jacqueline l. longe editor deirdre s. blanchfield associate editor volume a-b1', metadata={'source': '/media/supunlakshan/Learning Hub/AI & Machine Learning/LLM,OpenAI/End-to-End-Medical-Chatbot/data/Medical_book.pdf', 'page': 2}),
 Document(page_content='staff jacqueline l. longe project editor deirdre s. blanchfield associate editor christine b. jeryan managing editor donna olendorf senior editor stacey blachford associate editor kate kretschmann melissa c. mcdade ryan thomason assistant editors mark springer technical specialist andrea lopeman programmer/analyst barbara j. yarrow manager imaging multimedia content robyn v . young project manager imaging multimedia content dean dauphinais senio

## **Embedding**

In [13]:

from sentence_transformers import SentenceTransformer

# Extract text from Document objects
text_list = [t.page_content for t in text_chunks]

# Initialize SentenceTransformer model
model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')

# Encode the text chunks
embeddings = model.encode(text_list)

# Print the embeddings
print(embeddings)

/home/supunlakshan/anaconda3/envs/mchatbot/lib/python3.8/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/home/supunlakshan/anaconda3/envs/mchatbot/lib/python3.8/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


[[ 0.00174608 -0.03350287 -0.03290391 ... -0.00555645  0.10660913
   0.05099721]
 [-0.00524566 -0.01224833 -0.03722573 ...  0.0075348   0.08098163
   0.05183331]
 [ 0.02046325 -0.0224895  -0.00601478 ... -0.0070935  -0.00974825
   0.04680153]
 ...
 [-0.09775922  0.06158298 -0.04184233 ...  0.05067963 -0.04601221
  -0.07389956]
 [ 0.03905462  0.01553802 -0.0352585  ... -0.0279488  -0.05134996
   0.12449328]
 [ 0.01676182  0.05766533 -0.09481081 ... -0.04915264  0.03086303
   0.09051288]]


In [14]:
# Get the dimensions of the embeddings
embedding_dimensions = embeddings.shape

# Print the dimensions
print("Embedding dimensions:", embedding_dimensions)

print(type(embeddings))
print(len(embeddings))

Embedding dimensions: (4564, 384)
<class 'numpy.ndarray'>
4564


In [15]:
from pinecone import Pinecone

pc = Pinecone(api_key="afedfe83-ec30-4c3c-b51c-2e565474af4a")
index = pc.Index("mymchatbot")

In [16]:
# Specify your namespace
namespace = "book1"

In [17]:
import uuid
ids = [str(uuid.uuid4()) for _ in range(len(embeddings))]

print(len(ids))
print(ids)

4564
['5a076388-e2ea-4681-8747-329291e1c546', '12cc07a5-acfc-401c-b12d-cba55d4026a1', '4a878108-8d0a-4271-8dc2-035629711b3c', '90d1ca77-ef66-4c56-b60f-b79bc9ffcbbe', 'e01c6bcf-76cf-4c43-8623-d2b58ae11245', '1aac59d5-c5e7-4c17-b218-f8cda858f5e6', 'f27cc234-b5fb-4c50-8420-005fb36ab23a', '9838df2d-5edc-4fa0-846c-467f69dff7fb', '224c0055-fb5f-4bdc-a215-086dd557f11d', '15cfb6a5-2d45-442f-b25f-7c05ef4be2f1', '6f0bb720-8fa5-4e72-9f6b-ba0de60b365c', '09cda3ba-dfce-4be3-baaa-f169337fea65', '13fe48df-581b-4d48-8153-57f10f720710', '41ca8fe4-ef33-4837-947b-91739cad6ed1', '7691f61d-cd1b-4953-8b69-58317bb7c38c', '4a2c6925-ee58-4906-8da2-4f016916afb5', '389d4c9e-b759-4608-8938-8cd10ec4d465', '2996add7-0fcd-4e3a-9771-068f1c45e5e7', '27702eda-8bcb-4776-a9b7-151c1c37c99e', '62561faf-e7bc-46f0-8410-18cbcd543f5a', 'c061c3b3-ad16-4d7c-84d6-0f2b6e69e0ac', '8ef57d43-4dcf-47de-82f0-db237e011d68', '4f64d297-6bcb-472b-95d3-8085e16958cb', 'b6de7db2-7191-42c2-9891-c75124e6cc80', 'b0281529-eaa3-4f33-b582-5c62a63c0

In [18]:
vectors_to_upsert = [
    {
        "id": str(ids[i]),  # Ensure each ID is a string
        "values": embeddings[i],  # The embedding vector for the text chunk
        "metadata": {"page_content": str(text_chunks[i])}  # Storing page content as metadata
    } for i in range(len(embeddings))
]

In [19]:
print(type(vectors_to_upsert))
print(vectors_to_upsert[1000])

<class 'list'>
{'id': 'a4d4b8f7-538f-4b4e-ac1e-cf8f6024639b', 'values': array([-8.01913366e-02, -1.80788077e-02, -4.46191840e-02,  8.73805024e-03,
        2.60999287e-03, -3.64283212e-02,  2.15047840e-02,  9.04173180e-02,
       -9.81836766e-03, -4.85261902e-02,  6.05550893e-02,  2.02858467e-02,
       -2.65671797e-02,  6.19109347e-02, -1.14493676e-01,  1.52066126e-02,
       -2.99263857e-02,  3.37348767e-02, -1.78620107e-02,  9.84291881e-02,
        5.45518659e-03,  2.89662648e-02,  3.16723511e-02,  3.83103304e-02,
       -6.73435777e-02,  5.10734282e-02, -1.33403940e-02,  1.02279738e-01,
        7.22462237e-02, -1.10350326e-02,  8.78962781e-03,  1.06522284e-01,
       -3.43568102e-02,  2.39438415e-02, -7.40206102e-03,  2.38578655e-02,
       -4.30937931e-02,  2.95691788e-02, -4.33453433e-02,  8.59694369e-03,
        4.54146788e-03, -1.08812988e-01, -3.62280048e-02,  3.32686156e-02,
        1.19003616e-02, -1.19387448e-01, -2.21154261e-02,  6.84089065e-02,
       -2.10158937e-02,  9.6

In [20]:
# # Proceed with the upsert
# def upsert_in_batches(index, vectors, namespace, batch_size=100):
#     for i in range(0, len(vectors), batch_size):
#         batch = vectors[i:i+batch_size]
#         index.upsert(vectors=batch, namespace=namespace)

# # Usage
# upsert_in_batches(index, vectors_to_upsert, namespace, batch_size=100)

In [21]:
index.describe_index_stats()

{'dimension': 384,
 'index_fullness': 0.0,
 'namespaces': {'book1': {'vector_count': 4564}},
 'total_vector_count': 4564}

## **If we already have an index we can load it like this**

In [22]:
query=("what is the Autism?")

In [23]:
query_vector = model.encode(query)

In [24]:
print(query_vector.shape)
print(len(query_vector))
query_vector

(384,)
384


array([-1.84402205e-02,  3.09573207e-02, -5.37664630e-02,  4.13241833e-02,
       -1.43164108e-02,  3.40407528e-02,  8.38290751e-02,  4.32314388e-02,
       -7.74682090e-02,  3.24466191e-02,  4.01353203e-02, -1.70838889e-02,
       -5.79556599e-02,  2.44909003e-02, -7.58455321e-02,  2.53434144e-02,
       -1.75269190e-02, -4.07887734e-02, -2.63049570e-03,  1.99549627e-02,
       -2.69123036e-02,  7.74915591e-02, -1.41837010e-02, -7.40208030e-02,
       -4.22719680e-02,  7.01014698e-02,  3.07796113e-02, -1.37514427e-01,
        3.73859890e-02,  6.17686063e-02, -2.68634409e-02, -1.03813373e-01,
        8.36069137e-02,  8.33759978e-02, -6.26070723e-02,  5.68689927e-02,
        5.51290996e-02,  7.86005519e-03, -2.43740417e-02, -4.76878881e-02,
       -1.97741622e-03,  2.12764228e-03,  1.35273375e-02, -9.53048766e-02,
       -2.08564848e-02,  3.75018716e-02, -1.59766339e-03, -5.07076718e-02,
        3.45387869e-02,  7.57190958e-03, -2.20054053e-02, -1.97243523e-02,
       -4.10585722e-04,  

In [25]:
# Assuming `query_vector` is a numpy array
query_vector_list = query_vector.tolist()  # Convert numpy array to a list

query_result = index.query(
    vector=query_vector_list,  # Your query vector
    namespace="book1",
    top_k=5,  # Number of top similar vectors to retrieve
    include_metadata=True  # Ensure metadata is included in the response
)

In [26]:
# for match in query_result['matches']:
#     print(f"ID: {match['id']}, Score: {match['score']}, Page Content: {match['metadata'].get('page_content')}")

for match in query_result['matches']:
    print((f"{match['metadata'].get('page_content')}"))


page_content='autism research naar. http//www. naar.org. national information center children youth dis- abilities. http//www.nichcy.org/transitn.htm. carol a. turkington autograft seeskin grafting gale encyclopedia medicine 2 421autismgem - 0001 0432 - 10/22/03 143 pm page 421' metadata={'source': '/media/supunlakshan/Learning Hub/AI & Machine Learning/LLM,OpenAI/End-to-End-Medical-Chatbot/data/Medical_book.pdf', 'page': 434}
page_content='times often boys usual-ly first-born occurs around world racesand social backgrounds. autism usually evident thefirst three years life although children itshard tell problem develops. sometimes thecondition isnt diagnosed child enters school. person autism symptoms ranging mild severe 10 extraor-dinary ability one area mathematics mem-ory music art. children known autisticsavants formerly known idiot savants.. causes symptoms autism brain disorder affects way brain uses transmits information.' metadata={'source': '/media/supunlakshan/Learning Hub/AI

In [27]:
prompt_template="""
Use the following pieces of information to answer the user's question.
If you don't know the answer, just say that you don't know, don't try to make up an answer.

Context: {context}
Question: {question}

Only return the helpful answer below and nothing else.
Helpful answer:
"""

In [28]:
PROMPT=PromptTemplate(template=prompt_template, input_variables=["context", "question"])
chain_type_kwargs={"prompt": PROMPT}

In [29]:
llm = ctransformers.CTransformers(model="model/llama-2-7b-chat.ggmlv3.q4_0.bin",
                                  model_type="llama",
                                  config={'max_new_tokens': 512,
                                          'temperature': 0.8}
)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [30]:
from langchain_pinecone import PineconeVectorStore

# Assuming this is your sentence transformer model
model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')

# Create the PineconeVectorStore instance (assuming you have the index details)
vectorstore = PineconeVectorStore(index, model)

/home/supunlakshan/anaconda3/envs/mchatbot/lib/python3.8/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [31]:
from langchain.retrievers import SelfQueryRetriever

document_content_description = "page_content"
metadata_field_info = {}  # Define the metadata_field_info variable (if needed)

retriever = SelfQueryRetriever.from_llm(
    llm,
    vectorstore,
    document_content_description,
    metadata_field_info,
    enable_limit=True,
    verbose=True,
)


In [32]:
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",  # Replace "stuff" with your actual chain type name
    retriever=retriever,
)


In [33]:
import nltk  # Import for potential text truncation

def get_user_input():
  """Prompts the user for input and handles potential truncation."""
  max_tokens = 512  # Adjust this limit as needed
  while True:
    user_input = input(f"Input Prompt:")
    if len(nltk.word_tokenize(user_input)) <= max_tokens:  # Check token length
      return user_input
    else:
      print(f"Warning: Input exceeds maximum length ({max_tokens} tokens). Please try again with a shorter prompt.")

while True:
  user_input = get_user_input()  # Get user input with truncation handling

  # Embed the user query using encode
  query_vector = model.encode(user_input)

  try:
    # Use Langchain for retrieval and question answering (using invoke)
    result = qa.invoke({"query": query_vector.tolist()})
    print("Response :", result["result"])
  except Exception as e:
    print(f"An error occurred: {e}")
    print("Please try again with a different prompt.")


Number of tokens (9410) exceeded maximum context length (512).
